In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [2]:
# import sys
# !{sys.executable} -m install pandasql
# !{sys.executable} -m pip install pandas-profiling

In [3]:
mkdir inputs

A subdirectory or file inputs already exists.


In [4]:
mkdir outputs

A subdirectory or file outputs already exists.


In [5]:
import os
import json
import pandas as pd
from datetime import datetime
import pandasql as ps
import itertools
import re

In [6]:
from pandas_profiling import ProfileReport

Pandas backend loaded 1.2.4
Numpy backend loaded 1.20.1
Pyspark backend NOT loaded
Python backend loaded


In [7]:
pd.reset_option("display.max_rows")

In [8]:
pd.set_option('display.float_format', lambda x: '%.5f' % x)

In [9]:
# pd.set_option('display.max_rows', None)

In [10]:
CURRENT_WORKING_DIRECTORY = os.getcwd()
INPUTS = CURRENT_WORKING_DIRECTORY + "\\inputs"
OUTPUTS = CURRENT_WORKING_DIRECTORY + "\\outputs"
TICKETS = "tickets.xlsx"
TICKETS_LINES = "tickets_lines.xlsx"

In [11]:
CONFIG_FILE = "config.json"
with open(CURRENT_WORKING_DIRECTORY + "\\" + CONFIG_FILE, encoding='utf-8') as f:
    CONFIG = json.load(f)

In [12]:
TICKETS_DATES = CONFIG["TICKETS"]["DATES"]
TICKETS_SEPARATOR = CONFIG["TICKETS"]["SEPARATOR"]
TICKETS_DTYPE = CONFIG["TICKETS"]["DTYPE"]

In [13]:
TICKETS_LINES_DATES = CONFIG["TICKETS_LINES"]["DATES"]
TICKETS_LINES_SEPARATOR = CONFIG["TICKETS_LINES"]["SEPARATOR"]
TICKETS_LINES_DTYPE = CONFIG["TICKETS_LINES"]["DTYPE"]

In [14]:
WINNING_NUMBERS = CONFIG["WINNING_NUMBERS"]

In [15]:
WINNING_NUMBERS

['11', '19', '21', '33', '42']

In [16]:
# def myparser(x):
#     """
#     """
# #     try:
# #         datetime.utcfromtimestamp(int(x))
# #     except:
# #         return pd.NaT
#     return dt.datetime.strptime(x, '%Y-%m-%d %H:%M:%S')
# #    return datetime.utcfromtimestamp(int(x))

## TICKETS

In [17]:
tickets = pd.read_excel(
    INPUTS + "\\" + TICKETS,
    sheet_name="Sheet1",
    header=0,
    names=None,
    index_col=None,
    usecols=None,
    squeeze=None,
    dtype=None,
    engine="openpyxl",
    converters=None,
    true_values=None,
    false_values=None,
    skiprows=None,
    nrows=None,
    na_values=None,
    keep_default_na=True,
    na_filter=True,
    verbose=True,
    parse_dates=False,
    date_parser=None,
    thousands=None,
#   decimal='.',
    comment=None,
    skipfooter=0,
    convert_float=None,
    mangle_dupe_cols=True,
    storage_options=None
)

Reading sheet Sheet1


In [18]:
tickets.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5742 entries, 0 to 5741
Data columns (total 7 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   drawing_id           5742 non-null   object        
 1   drawingdate          5742 non-null   datetime64[ns]
 2   tickets_id           5742 non-null   object        
 3   shares               5742 non-null   float64       
 4   total_shares         5742 non-null   float64       
 5   fraction             5742 non-null   float64       
 6   participation_state  5742 non-null   object        
dtypes: datetime64[ns](1), float64(3), object(3)
memory usage: 314.1+ KB


In [19]:
tickets.sample(3)

drawing_id         drawingdate                tickets_id  \
928   polishMiniLotto_3892 2020-06-28 19:50:00  5ef0c758877558002cbca210   
2370  polishMiniLotto_3892 2020-06-28 19:50:00  5ef838b598953a002c5d4e76   
4729  polishMiniLotto_3892 2020-06-28 19:50:00  5ef7a7b1bc5fd30028bfafbf   

      shares  total_shares  fraction participation_state  
928  1.00000       1.00000   1.00000            FINISHED  
2370 1.00000       1.00000   1.00000            FINISHED  
4729 1.00000       1.00000   1.00000            FINISHED

In [20]:
tickets["drawing_id"].unique()

array(['polishMiniLotto_3892'], dtype=object)

In [21]:
tickets["drawing_id"].nunique()

1

In [22]:
tickets["drawingdate"].unique()

array(['2020-06-28T19:50:00.000000000'], dtype='datetime64[ns]')

In [23]:
tickets["drawingdate"].nunique()

1

In [24]:
tickets["tickets_id"].unique()

array(['5e3fdd6c6d0034002c62ce11', '5924d5c5b9b5ab77047f1238',
       '5ea0e78a0fa635002cfbab70', ..., '5ef8a54fc5d9eb002705e1df',
       '5ef8a555b0deeb0027356946', '5ef8a567c5d9eb002705e1f0'],
      dtype=object)

In [25]:
tickets["tickets_id"].nunique()

5742

In [26]:
tickets["shares"].unique()

array([  1.,   2.,   3., 128., 256.])

In [27]:
tickets["shares"].nunique()

5

In [28]:
tickets["total_shares"].unique()

array([1.000e+00, 7.700e+01, 3.000e+01, 9.000e+01, 4.100e+01, 1.024e+03])

In [29]:
tickets["total_shares"].nunique()

6

In [30]:
tickets["fraction"].unique()

array([1.     , 0.01299, 0.03333, 0.02597, 0.01111, 0.03896, 0.02439,
       0.125  , 0.25   ])

In [31]:
tickets["fraction"].nunique()

9

In [32]:
tickets["participation_state"].unique()

array(['FINISHED'], dtype=object)

In [33]:
tickets["participation_state"].nunique()

1

In [34]:
tickets.describe()

shares  total_shares   fraction
count 5742.00000    5742.00000 5742.00000
mean     1.50958       5.10728    0.99244
std      8.37054      63.27480    0.08334
min      1.00000       1.00000    0.01111
25%      1.00000       1.00000    1.00000
50%      1.00000       1.00000    1.00000
75%      1.00000       1.00000    1.00000
max    256.00000    1024.00000    1.00000

In [35]:
tickets

drawing_id         drawingdate                tickets_id  \
0     polishMiniLotto_3892 2020-06-28 19:50:00  5e3fdd6c6d0034002c62ce11   
1     polishMiniLotto_3892 2020-06-28 19:50:00  5924d5c5b9b5ab77047f1238   
2     polishMiniLotto_3892 2020-06-28 19:50:00  5ea0e78a0fa635002cfbab70   
3     polishMiniLotto_3892 2020-06-28 19:50:00  5ea33280dd5890002d9caab0   
4     polishMiniLotto_3892 2020-06-28 19:50:00  5920a5739abd3c607d351d74   
...                    ...                 ...                       ...   
5737  polishMiniLotto_3892 2020-06-28 19:50:00  5ef8a507b0deeb002735693a   
5738  polishMiniLotto_3892 2020-06-28 19:50:00  5ef8a50fbc5fd30028bfe05c   
5739  polishMiniLotto_3892 2020-06-28 19:50:00  5ef8a54fc5d9eb002705e1df   
5740  polishMiniLotto_3892 2020-06-28 19:50:00  5ef8a555b0deeb0027356946   
5741  polishMiniLotto_3892 2020-06-28 19:50:00  5ef8a567c5d9eb002705e1f0   

      shares  total_shares  fraction participation_state  
0    1.00000       1.00000   1.00000            FINISHED  
1    1.00000       1.00000   1.00000            FINISHED  
2    1.00000       1.00000   1.00000            FINISHED  
3    1.00000       1.00000   1.00000            FINISHED  
4    1.00000       1.00000   1.00000            FINISHED  
...      ...           ...       ...                 ...  
5737 1.00000       1.00000   1.00000            FINISHED  
5738 1.00000       1.00000   1.00000            FINISHED  
5739 1.00000       1.00000   1.00000            FINISHED  
5740 1.00000       1.00000   1.00000            FINISHED  
5741 1.00000       1.00000   1.00000            FINISHED  

[5742 rows x 7 columns]

In [36]:
tickets.to_csv(OUTPUTS + "\\tickets.csv")

## tickets profiling

In [37]:
tickets_profile = ProfileReport(tickets, explorative=True)

In [38]:
tickets_profile.to_file(output_file=OUTPUTS + "\\tickets_profile.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Note: NumExpr detected 16 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
NumExpr defaulting to 8 threads.


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [39]:
tickets_profile.to_notebook_iframe()

## TICKETS_LINES

In [40]:
tickets_lines = pd.read_excel(
    INPUTS + "\\" + TICKETS_LINES,
    sheet_name="Sheet1",
    header=0,
    names=None,
    index_col=None,
    usecols=None,
    squeeze=None,
    dtype=None,
    engine="openpyxl",
    converters=None,
    true_values=None,
    false_values=None,
    skiprows=None,
    nrows=None,
    na_values=None,
    keep_default_na=True,
    na_filter=True,
    verbose=True,
    parse_dates=False,
    date_parser=None,
    thousands=None,
#   decimal='.',
    comment=None,
    skipfooter=0,
    convert_float=None,
    mangle_dupe_cols=True,
    storage_options=None
)

Reading sheet Sheet1


In [41]:
tickets_lines.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 22351 entries, 0 to 22350
Data columns (total 5 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   tickets_id  22351 non-null  object 
 1   drawing_id  22351 non-null  object 
 2   line_id     22351 non-null  float64
 3   bet_type    22351 non-null  object 
 4   numbers     22351 non-null  object 
dtypes: float64(1), object(4)
memory usage: 873.2+ KB


In [42]:
tickets_lines.sample(3)

tickets_id            drawing_id  line_id bet_type  \
4170   5ef7a7a7bc5fd30028bfae73  polishMiniLotto_3892 10.00000   NORMAL   
13077  5ef87b4ec5d9eb002705d9d1  polishMiniLotto_3892  2.00000   NORMAL   
9893   5ef84365223ea4002c608907  polishMiniLotto_3892  4.00000   NORMAL   

                      numbers  
4170     1 , 5 , 18 , 23 , 32  
13077  11 , 14 , 24 , 38 , 41  
9893   11 , 21 , 33 , 34 , 37

In [43]:
tickets_lines["tickets_id"].unique()

array(['550b11cee4b07489e9e03217', '553a820ce4b0a8a498faab3a',
       '553bcf70e4b0f1fa230477c8', ..., '5ef8f380d4b758002c5b5d72',
       '5ef8f3de311e0b002cfcec6c', '5ef8f406b8b7d8002df3b0c3'],
      dtype=object)

In [44]:
tickets_lines["tickets_id"].nunique()

5742

In [45]:
tickets_lines["drawing_id"].unique()

array(['polishMiniLotto_3892'], dtype=object)

In [46]:
tickets_lines["drawing_id"].nunique()

1

In [47]:
tickets_lines["line_id"].unique()

array([ 1.,  2.,  3.,  4.,  5.,  6.,  7.,  8.,  9., 10., 11., 12.])

In [48]:
tickets_lines["line_id"].nunique()

12

In [49]:
tickets_lines["bet_type"].unique()

array(['NORMAL', 'S0600', 'S0700', 'S0800', 'S1000', 'S0900'],
      dtype=object)

In [50]:
tickets_lines["bet_type"].nunique()

6

In [51]:
tickets_lines["numbers"].unique()

array(['3 , 4 , 6 , 7 , 36', '7 , 25 , 29 , 33 , 39',
       '4 , 13 , 24 , 26 , 29', ..., '8 , 19 , 21 , 28 , 33',
       '3 , 10 , 12 , 20 , 39', '14 , 24 , 25 , 28 , 31'], dtype=object)

In [52]:
tickets_lines["numbers"].nunique()

18214

In [53]:
pd.get_option("display.max_rows")

60

In [54]:
pd.options.display.max_rows = 20

In [55]:
print(tickets_lines[tickets_lines["tickets_id"] == "5ef88375c5d9eb002705db0c"])

                     tickets_id            drawing_id  line_id bet_type  \
13568  5ef88375c5d9eb002705db0c  polishMiniLotto_3892  1.00000   NORMAL   
13569  5ef88375c5d9eb002705db0c  polishMiniLotto_3892  2.00000   NORMAL   
13570  5ef88375c5d9eb002705db0c  polishMiniLotto_3892  3.00000   NORMAL   
13571  5ef88375c5d9eb002705db0c  polishMiniLotto_3892  4.00000   NORMAL   
13572  5ef88375c5d9eb002705db0c  polishMiniLotto_3892  5.00000   NORMAL   
13573  5ef88375c5d9eb002705db0c  polishMiniLotto_3892  6.00000   NORMAL   
13574  5ef88375c5d9eb002705db0c  polishMiniLotto_3892  7.00000   NORMAL   
13575  5ef88375c5d9eb002705db0c  polishMiniLotto_3892  8.00000   NORMAL   
13576  5ef88375c5d9eb002705db0c  polishMiniLotto_3892  9.00000   NORMAL   
13577  5ef88375c5d9eb002705db0c  polishMiniLotto_3892 10.00000   NORMAL   
13578  5ef88375c5d9eb002705db0c  polishMiniLotto_3892 11.00000   NORMAL   
13579  5ef88375c5d9eb002705db0c  polishMiniLotto_3892 12.00000   NORMAL   

                     num

### REMOVING BLANKS

In [56]:
tickets_lines["numbers"] = tickets_lines["numbers"].str.replace(' ', '')

In [57]:
# print(tickets[tickets["tickets_id"] == "5ef88375c5d9eb002705db0c"])

In [58]:
# print(tickets_lines[tickets_lines["tickets_id"] == "5ef88375c5d9eb002705db0c"])

### TRANSFORMING STRING TO LIST

In [59]:
tickets_lines['numbers_list'] = tickets_lines["numbers"].apply(lambda x: x.strip('()').split(','))

In [60]:
tickets_lines

tickets_id            drawing_id  line_id bet_type  \
0      550b11cee4b07489e9e03217  polishMiniLotto_3892  1.00000   NORMAL   
1      553a820ce4b0a8a498faab3a  polishMiniLotto_3892  1.00000   NORMAL   
2      553bcf70e4b0f1fa230477c8  polishMiniLotto_3892  1.00000   NORMAL   
3      55407a30e4b08fc8150fb94b  polishMiniLotto_3892  1.00000   NORMAL   
4      5545f560e4b0d4bda5336c8a  polishMiniLotto_3892  1.00000   NORMAL   
...                         ...                   ...      ...      ...   
22346  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892  8.00000   NORMAL   
22347  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892  9.00000   NORMAL   
22348  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892 10.00000   NORMAL   
22349  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892 11.00000   NORMAL   
22350  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892 12.00000   NORMAL   

              numbers          numbers_list  
0          3,4,6,7,36      [3, 4, 6, 7, 36]  
1       7,25,29,33,39   [7, 25, 29, 33, 39]  
2       4,13,24,26,29   [4, 13, 24, 26, 29]  
3       6,21,27,31,37   [6, 21, 27, 31, 37]  
4       8,13,21,25,30   [8, 13, 21, 25, 30]  
...               ...                   ...  
22346  13,16,26,38,40  [13, 16, 26, 38, 40]  
22347     1,2,7,31,36     [1, 2, 7, 31, 36]  
22348   8,19,21,28,33   [8, 19, 21, 28, 33]  
22349   3,10,12,20,39   [3, 10, 12, 20, 39]  
22350  14,24,25,28,31  [14, 24, 25, 28, 31]  

[22351 rows x 6 columns]

### AN EXAMPLE OF S0800 BET

In [61]:
tickets_lines["numbers"][7228]

'5,8,11,16,17,19,21,33'

In [62]:
tickets_lines["numbers_list"][7228]

['5', '8', '11', '16', '17', '19', '21', '33']

In [63]:
WINNING_NUMBERS

['11', '19', '21', '33', '42']

In [64]:
"11" in tickets_lines["numbers_list"][7228]

True

In [65]:
matched_numbers = [X for X in WINNING_NUMBERS if(X in tickets_lines["numbers_list"][7228])]

In [66]:
matched_numbers

['11', '19', '21', '33']

In [67]:
len(matched_numbers)

4

In [68]:
tickets_lines.shape[0]

22351

In [69]:
cols = [
    "tickets_id",
    "drawing_id",
    "line_id",
    "bet_type",
    "numbers",
    "numbers_list",
    'matched_numbers',
    'matched_numbers_count'
]

df_matched_numbers = pd.DataFrame(columns = cols)
for i in range(tickets_lines.shape[0]):
    print("Processing: ")
    print(tickets_lines["numbers_list"][int(i)])
#     rstr = ''.join(str(rows_5[i][0]))
#     row = tickets_lines[tickets_lines["numbers"].str.contains(rstr, na=False)]
    matched_numbers = [X for X in WINNING_NUMBERS if(X in tickets_lines["numbers_list"][int(i)])]
    print("Matched numbers: ")
    print(matched_numbers)
#     df_winning_numbers = df_winning_numbers.append(matched_numbers)
#     tickets_lines["matched_numbers"].append('0')
    df_matched_numbers = df_matched_numbers.append(
        {
            "tickets_id": tickets_lines["tickets_id"][int(i)],
            "drawing_id": tickets_lines["drawing_id"][int(i)],
            "line_id": tickets_lines["line_id"][int(i)],
            "bet_type": tickets_lines["bet_type"][int(i)],
            "numbers": tickets_lines["numbers"][int(i)],
            "numbers_list": tickets_lines["numbers_list"][int(i)],
            'matched_numbers': matched_numbers,
            'matched_numbers_count': len(matched_numbers)
        },
        ignore_index=True
    )
#     tickets_lines_with_matched_numbers = tickets_lines_with_matched_numbers.append({'matched_numbers': matched_numbers, 'matched_numbers_count': len(matched_numbers)}, ignore_index=True)

Processing: 
['3', '4', '6', '7', '36']
Matched numbers: 
[]
Processing: 
['7', '25', '29', '33', '39']
Matched numbers: 
['33']
Processing: 
['4', '13', '24', '26', '29']
Matched numbers: 
[]
Processing: 
['6', '21', '27', '31', '37']
Matched numbers: 
['21']
Processing: 
['8', '13', '21', '25', '30']
Matched numbers: 
['21']
Processing: 
['4', '16', '27', '31', '40']
Matched numbers: 
[]
Processing: 
['3', '7', '19', '20', '31']
Matched numbers: 
['19']
Processing: 
['1', '18', '30', '39', '42']
Matched numbers: 
['42']
Processing: 
['3', '13', '24', '28', '30']
Matched numbers: 
[]
Processing: 
['1', '24', '28', '36', '38']
Matched numbers: 
[]
Processing: 
['2', '3', '9', '33', '40']
Matched numbers: 
['33']
Processing: 
['3', '9', '13', '18', '28']
Matched numbers: 
[]
Processing: 
['3', '16', '18', '19', '41']
Matched numbers: 
['19']
Processing: 
['1', '5', '11', '21', '40']
Matched numbers: 
['11', '21']
Processing: 
['13', '25', '36', '38', '42']
Matched numbers: 
['42']
Proce

Processing: 
['9', '13', '27', '34', '37']
Matched numbers: 
[]
Processing: 
['3', '7', '19', '25', '33']
Matched numbers: 
['19', '33']
Processing: 
['6', '10', '15', '25', '36']
Matched numbers: 
[]
Processing: 
['2', '5', '9', '16', '19']
Matched numbers: 
['19']
Processing: 
['6', '11', '21', '23', '27']
Matched numbers: 
['11', '21']
Processing: 
['17', '20', '31', '33', '34']
Matched numbers: 
['33']
Processing: 
['1', '14', '24', '41', '42']
Matched numbers: 
['42']
Processing: 
['9', '22', '27', '36', '38']
Matched numbers: 
[]
Processing: 
['1', '7', '8', '19', '24']
Matched numbers: 
['19']
Processing: 
['2', '11', '14', '22', '25']
Matched numbers: 
['11']
Processing: 
['6', '11', '24', '26', '42']
Matched numbers: 
['11', '42']
Processing: 
['1', '10', '18', '28', '36']
Matched numbers: 
[]
Processing: 
['1', '4', '6', '7', '37']
Matched numbers: 
[]
Processing: 
['11', '13', '27', '38', '39']
Matched numbers: 
['11']
Processing: 
['5', '13', '18', '28', '38']
Matched numbe

Processing: 
['7', '13', '21', '23', '34']
Matched numbers: 
['21']
Processing: 
['8', '10', '15', '18', '32']
Matched numbers: 
[]
Processing: 
['5', '13', '21', '27', '28']
Matched numbers: 
['21']
Processing: 
['10', '12', '25', '26', '29']
Matched numbers: 
[]
Processing: 
['7', '24', '28', '30', '39']
Matched numbers: 
[]
Processing: 
['9', '12', '16', '35', '37']
Matched numbers: 
[]
Processing: 
['8', '15', '19', '21', '34']
Matched numbers: 
['19', '21']
Processing: 
['1', '8', '12', '16', '21']
Matched numbers: 
['21']
Processing: 
['1', '7', '24', '37', '41']
Matched numbers: 
[]
Processing: 
['1', '6', '9', '27', '29']
Matched numbers: 
[]
Processing: 
['7', '13', '21', '27', '28']
Matched numbers: 
['21']
Processing: 
['8', '9', '10', '31', '40']
Matched numbers: 
[]
Processing: 
['19', '26', '31', '32', '33']
Matched numbers: 
['19', '33']
Processing: 
['27', '31', '34', '38', '42']
Matched numbers: 
['42']
Processing: 
['12', '16', '35', '37', '41']
Matched numbers: 
[]
P

Processing: 
['27', '31', '36', '37', '40']
Matched numbers: 
[]
Processing: 
['1', '4', '10', '18', '36']
Matched numbers: 
[]
Processing: 
['12', '13', '26', '39', '42']
Matched numbers: 
['42']
Processing: 
['3', '6', '17', '20', '26']
Matched numbers: 
[]
Processing: 
['1', '3', '6', '8', '33']
Matched numbers: 
['33']
Processing: 
['8', '10', '18', '21', '23']
Matched numbers: 
['21']
Processing: 
['4', '6', '32', '34', '35']
Matched numbers: 
[]
Processing: 
['6', '10', '39', '40', '42']
Matched numbers: 
['42']
Processing: 
['3', '13', '15', '25', '33']
Matched numbers: 
['33']
Processing: 
['4', '11', '21', '27', '37']
Matched numbers: 
['11', '21']
Processing: 
['3', '11', '15', '21', '27']
Matched numbers: 
['11', '21']
Processing: 
['13', '15', '27', '36', '40']
Matched numbers: 
[]
Processing: 
['4', '19', '21', '35', '38']
Matched numbers: 
['19', '21']
Processing: 
['4', '12', '14', '30', '33']
Matched numbers: 
['33']
Processing: 
['2', '5', '9', '24', '35']
Matched numb

Processing: 
['6', '8', '16', '17', '34']
Matched numbers: 
[]
Processing: 
['4', '8', '18', '19', '29']
Matched numbers: 
['19']
Processing: 
['10', '16', '26', '28', '29']
Matched numbers: 
[]
Processing: 
['7', '10', '23', '30', '39']
Matched numbers: 
[]
Processing: 
['3', '15', '29', '32', '33']
Matched numbers: 
['33']
Processing: 
['7', '8', '20', '27', '29']
Matched numbers: 
[]
Processing: 
['6', '22', '28', '32', '40']
Matched numbers: 
[]
Processing: 
['6', '15', '22', '29', '38']
Matched numbers: 
[]
Processing: 
['4', '7', '27', '35', '41']
Matched numbers: 
[]
Processing: 
['4', '18', '23', '33', '36']
Matched numbers: 
['33']
Processing: 
['3', '20', '24', '28', '41']
Matched numbers: 
[]
Processing: 
['4', '12', '16', '19', '22']
Matched numbers: 
['19']
Processing: 
['5', '9', '16', '20', '36']
Matched numbers: 
[]
Processing: 
['1', '21', '25', '38', '39']
Matched numbers: 
['21']
Processing: 
['1', '5', '7', '15', '23']
Matched numbers: 
[]
Processing: 
['17', '20', 

...

Processing: 
['32', '37', '39', '40', '42']
Matched numbers: 
['42']
Processing: 
['3', '8', '17', '29', '36']
Matched numbers: 
[]
Processing: 
['5', '8', '17', '18', '31']
Matched numbers: 
[]
Processing: 
['1', '22', '26', '30', '33']
Matched numbers: 
['33']
Processing: 
['6', '16', '17', '33', '42']
Matched numbers: 
['33', '42']
Processing: 
['3', '15', '22', '26', '40']
Matched numbers: 
[]
Processing: 
['3', '11', '12', '32', '35']
Matched numbers: 
['11']
Processing: 
['2', '5', '14', '32', '41']
Matched numbers: 
[]
Processing: 
['2', '6', '18', '33', '37']
Matched numbers: 
['33']
Processing: 
['1', '2', '9', '11', '31']
Matched numbers: 
['11']
Processing: 
['3', '6', '11', '20', '29']
Matched numbers: 
['11']
Processing: 
['11', '18', '20', '26', '42']
Matched numbers: 
['11', '42']
Processing: 
['2', '21', '33', '38', '41']
Matched numbers: 
['21', '33']
Processing: 
['10', '16', '26', '33', '41']
Matched numbers: 
['33']
Processing: 
['11', '12', '17', '20', '21']
Matche

Processing: 
['2', '6', '28', '29', '34']
Matched numbers: 
[]
Processing: 
['13', '19', '22', '34', '41']
Matched numbers: 
['19']
Processing: 
['3', '4', '14', '23', '26']
Matched numbers: 
[]
Processing: 
['2', '26', '30', '34', '40']
Matched numbers: 
[]
Processing: 
['18', '24', '32', '33', '40']
Matched numbers: 
['33']
Processing: 
['8', '12', '14', '31', '34']
Matched numbers: 
[]
Processing: 
['1', '5', '8', '11', '17']
Matched numbers: 
['11']
Processing: 
['1', '8', '26', '27', '41']
Matched numbers: 
[]
Processing: 
['30', '34', '37', '38', '40']
Matched numbers: 
[]
Processing: 
['4', '11', '16', '27', '33']
Matched numbers: 
['11', '33']
Processing: 
['9', '10', '24', '34', '41']
Matched numbers: 
[]
Processing: 
['13', '16', '17', '31', '33']
Matched numbers: 
['33']
Processing: 
['5', '18', '22', '38', '41']
Matched numbers: 
[]
Processing: 
['14', '17', '19', '27', '42']
Matched numbers: 
['19', '42']
Processing: 
['1', '5', '23', '30', '33']
Matched numbers: 
['33']
P

Processing: 
['13', '16', '29', '34', '36']
Matched numbers: 
[]
Processing: 
['18', '21', '27', '28', '32']
Matched numbers: 
['21']
Processing: 
['2', '23', '24', '25', '39']
Matched numbers: 
[]
Processing: 
['7', '8', '18', '30', '34']
Matched numbers: 
[]
Processing: 
['11', '20', '25', '26', '40']
Matched numbers: 
['11']
Processing: 
['1', '20', '21', '26', '31']
Matched numbers: 
['21']
Processing: 
['5', '15', '18', '32', '37']
Matched numbers: 
[]
Processing: 
['9', '24', '27', '29', '42']
Matched numbers: 
['42']
Processing: 
['1', '16', '17', '38', '41']
Matched numbers: 
[]
Processing: 
['9', '15', '18', '20', '34']
Matched numbers: 
[]
Processing: 
['1', '2', '15', '20', '25']
Matched numbers: 
[]
Processing: 
['3', '5', '13', '30', '35']
Matched numbers: 
[]
Processing: 
['7', '18', '22', '29', '41']
Matched numbers: 
[]
Processing: 
['2', '25', '28', '30', '34']
Matched numbers: 
[]
Processing: 
['5', '7', '10', '19', '41']
Matched numbers: 
['19']
Processing: 
['13', '

Processing: 
['11', '12', '15', '17', '41']
Matched numbers: 
['11']
Processing: 
['8', '15', '23', '30', '35']
Matched numbers: 
[]
Processing: 
['8', '12', '31', '37', '42']
Matched numbers: 
['42']
Processing: 
['1', '21', '24', '39', '42']
Matched numbers: 
['21', '42']
Processing: 
['3', '9', '14', '38', '41']
Matched numbers: 
[]
Processing: 
['3', '11', '27', '34', '42']
Matched numbers: 
['11', '42']
Processing: 
['2', '6', '7', '14', '26']
Matched numbers: 
[]
Processing: 
['1', '5', '22', '28', '30']
Matched numbers: 
[]
Processing: 
['3', '4', '12', '18', '32']
Matched numbers: 
[]
Processing: 
['2', '23', '25', '39', '41']
Matched numbers: 
[]
Processing: 
['25', '29', '30', '33', '37']
Matched numbers: 
['33']
Processing: 
['9', '13', '15', '20', '24']
Matched numbers: 
[]
Processing: 
['1', '2', '4', '7', '15']
Matched numbers: 
[]
Processing: 
['17', '19', '29', '33', '36']
Matched numbers: 
['19', '33']
Processing: 
['11', '14', '26', '38', '40']
Matched numbers: 
['11'

Processing: 
['6', '15', '24', '33', '37']
Matched numbers: 
['33']
Processing: 
['5', '10', '11', '17', '33']
Matched numbers: 
['11', '33']
Processing: 
['6', '23', '29', '38', '39']
Matched numbers: 
[]
Processing: 
['2', '10', '11', '27', '32']
Matched numbers: 
['11']
Processing: 
['12', '19', '28', '36', '42']
Matched numbers: 
['19', '42']
Processing: 
['1', '7', '14', '23', '33']
Matched numbers: 
['33']
Processing: 
['13', '15', '28', '39', '40']
Matched numbers: 
[]
Processing: 
['11', '19', '23', '31', '40']
Matched numbers: 
['11', '19']
Processing: 
['5', '14', '16', '22', '40']
Matched numbers: 
[]
Processing: 
['1', '2', '9', '26', '30']
Matched numbers: 
[]
Processing: 
['2', '22', '25', '27', '41']
Matched numbers: 
[]
Processing: 
['1', '28', '29', '41', '42']
Matched numbers: 
['42']
Processing: 
['3', '7', '20', '28', '34']
Matched numbers: 
[]
Processing: 
['2', '10', '24', '36', '40']
Matched numbers: 
[]
Processing: 
['3', '5', '14', '27', '34']
Matched numbers: 

In [70]:
df_matched_numbers

tickets_id            drawing_id  line_id bet_type  \
0      550b11cee4b07489e9e03217  polishMiniLotto_3892  1.00000   NORMAL   
1      553a820ce4b0a8a498faab3a  polishMiniLotto_3892  1.00000   NORMAL   
2      553bcf70e4b0f1fa230477c8  polishMiniLotto_3892  1.00000   NORMAL   
3      55407a30e4b08fc8150fb94b  polishMiniLotto_3892  1.00000   NORMAL   
4      5545f560e4b0d4bda5336c8a  polishMiniLotto_3892  1.00000   NORMAL   
...                         ...                   ...      ...      ...   
22346  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892  8.00000   NORMAL   
22347  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892  9.00000   NORMAL   
22348  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892 10.00000   NORMAL   
22349  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892 11.00000   NORMAL   
22350  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892 12.00000   NORMAL   

              numbers          numbers_list matched_numbers  \
0          3,4,6,7,36      [3, 4, 6, 7, 36]              []   
1       7,25,29,33,39   [7, 25, 29, 33, 39]            [33]   
2       4,13,24,26,29   [4, 13, 24, 26, 29]              []   
3       6,21,27,31,37   [6, 21, 27, 31, 37]            [21]   
4       8,13,21,25,30   [8, 13, 21, 25, 30]            [21]   
...               ...                   ...             ...   
22346  13,16,26,38,40  [13, 16, 26, 38, 40]              []   
22347     1,2,7,31,36     [1, 2, 7, 31, 36]              []   
22348   8,19,21,28,33   [8, 19, 21, 28, 33]    [19, 21, 33]   
22349   3,10,12,20,39   [3, 10, 12, 20, 39]              []   
22350  14,24,25,28,31  [14, 24, 25, 28, 31]              []   

      matched_numbers_count  
0                         0  
1                         1  
2                         0  
3                         1  
4                         1  
...                     ...  
22346                     0  
22347                     0  
22348                     3  
22349                     0  
22350                     0  

[22351 rows x 8 columns]

In [71]:
df_matched_numbers.to_csv(OUTPUTS + "\\df_matched_numbers.csv")

### count prizes

* Prize table
    * Tier 1 (match 5 numbers) = 90,000 EUR
    * Tier 2 (match 4 numbers) = 200 EUR
    * Tier 3 (match 3 numbers) = 5 EUR

In [72]:
df_matched_numbers["bet_type"].unique()

array(['NORMAL', 'S0600', 'S0700', 'S0800', 'S1000', 'S0900'],
      dtype=object)

### no prize

In [73]:
df_matched_numbers['prize'] = 0

### NORMAL - Tier 1 (match 5 numbers) = 90000 EUR

In [74]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["NORMAL"])) & (df_matched_numbers['matched_numbers_count'].isin([5]))), 'prize'
] = 1 * 90000 + 0 * 200 + 0 * 5

### NORMAL - Tier 2 (match 4 numbers) = 200 EUR

In [75]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["NORMAL"])) & (df_matched_numbers['matched_numbers_count'].isin([4]))), 'prize'
] = 0 * 90000 + 1 * 200 + 0 * 5

### NORMAL - Tier 3 (match 3 numbers) = 5 EUR

In [76]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["NORMAL"])) & (df_matched_numbers['matched_numbers_count'].isin([3]))), 'prize'
] = 0 * 90000 + 0 * 200 + 1 * 5

### S0600 - Tier 1 (match 5 numbers) = 90000 EUR and more

In [77]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S0600"])) & (df_matched_numbers['matched_numbers_count'].isin([5]))), 'prize'
] = 1 * 90000 + 5 * 200 + 0 * 5

### S0600 - Tier 2 (match 4 numbers) = 200 EUR and more

In [78]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S0600"])) & (df_matched_numbers['matched_numbers_count'].isin([4]))), 'prize'
] = 0 * 90000 + 2 * 200 + 4 * 5

### S0600 - Tier 3 (match 3 numbers) = 5 EUR and more

In [79]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S0600"])) & (df_matched_numbers['matched_numbers_count'].isin([3]))), 'prize'
] = 0 * 90000 + 0 * 200 + 3 * 5

### S0700 - Tier 1 (match 5 numbers) = 90000 EUR and more

In [80]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S0700"])) & (df_matched_numbers['matched_numbers_count'].isin([5]))), 'prize'
] = 1 * 90000 + 10 * 200 + 10 * 5

### S0700 - Tier 2 (match 4 numbers) = 200 EUR and more

In [81]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S0700"])) & (df_matched_numbers['matched_numbers_count'].isin([4]))), 'prize'
] = 0 * 90000 + 3 * 200 + 12 * 5

### S0700 - Tier 3 (match 3 numbers) = 5 EUR and more

In [82]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S0700"])) & (df_matched_numbers['matched_numbers_count'].isin([3]))), 'prize'
] = 0 * 90000 + 0 * 200 + 6 * 5

### S0800 - Tier 1 (match 5 numbers) = 90000 EUR and more

In [83]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S0800"])) & (df_matched_numbers['matched_numbers_count'].isin([5]))), 'prize'
] = 1 * 90000 + 15 * 200 + 30 * 5

### S0800 - Tier 2 (match 4 numbers) = 200 EUR and more

In [84]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S0800"])) & (df_matched_numbers['matched_numbers_count'].isin([4]))), 'prize'
] = 0 * 90000 + 4 * 200 + 24 * 5

### S0800 - Tier 3 (match 3 numbers) = 5 EUR and more

In [85]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S0800"])) & (df_matched_numbers['matched_numbers_count'].isin([3]))), 'prize'
] = 0 * 90000 + 0 * 200 + 10 * 5

### S0900 - Tier 1 (match 5 numbers) = 90000 EUR and more

In [86]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S0900"])) & (df_matched_numbers['matched_numbers_count'].isin([5]))), 'prize'
] = 1 * 90000 + 20 * 200 + 60 * 5

### S0900 - Tier 2 (match 4 numbers) = 200 EUR and more

In [87]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S0900"])) & (df_matched_numbers['matched_numbers_count'].isin([4]))), 'prize'
] = 0 * 90000 + 5 * 200 + 40 * 5

### S0900 - Tier 3 (match 3 numbers) = 5 EUR and more

In [88]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S0900"])) & (df_matched_numbers['matched_numbers_count'].isin([3]))), 'prize'
] = 0 * 90000 + 0 * 200 + 15 * 5

### S1000 - Tier 1 (match 5 numbers) = 90000 EUR and more

In [89]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S1000"])) & (df_matched_numbers['matched_numbers_count'].isin([5]))), 'prize'
] = 1 * 90000 + 25 * 200 + 100 * 5

### S1000 - Tier 2 (match 4 numbers) = 200 EUR and more

In [90]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S1000"])) & (df_matched_numbers['matched_numbers_count'].isin([4]))), 'prize'
] = 0 * 90000 + 6 * 200 + 60 * 5

### S1000 - Tier 3 (match 3 numbers) = 5 EUR and more

In [91]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S1000"])) & (df_matched_numbers['matched_numbers_count'].isin([3]))), 'prize'
] = 0 * 90000 + 0 * 200 + 21 * 5

### S1100 - Tier 1 (match 5 numbers) = 90000 EUR and more

In [92]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S1100"])) & (df_matched_numbers['matched_numbers_count'].isin([5]))), 'prize'
] = 1 * 90000 + 30 * 200 + 150 * 5

### S1100 - Tier 2 (match 4 numbers) = 200 EUR and more

In [93]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S1100"])) & (df_matched_numbers['matched_numbers_count'].isin([4]))), 'prize'
] = 0 * 90000 + 7 * 200 + 84 * 5

### S1100 - Tier 3 (match 3 numbers) = 5 EUR and more

In [94]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S1100"])) & (df_matched_numbers['matched_numbers_count'].isin([3]))), 'prize'
] = 0 * 90000 + 0 * 200 + 28 * 5

### S1200 - Tier 1 (match 5 numbers) = 90000 EUR and more

In [95]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S1200"])) & (df_matched_numbers['matched_numbers_count'].isin([5]))), 'prize'
] = 1 * 90000 + 35 * 200 + 210 * 5

### S1200 - Tier 2 (match 4 numbers) = 200 EUR and more

In [96]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S1200"])) & (df_matched_numbers['matched_numbers_count'].isin([4]))), 'prize'
] = 0 * 90000 + 8 * 200 + 112 * 5

### S1200 - Tier 3 (match 3 numbers) = 5 EUR and more

In [97]:
df_matched_numbers.loc[
    ((df_matched_numbers['bet_type'].isin(["S1200"])) & (df_matched_numbers['matched_numbers_count'].isin([3]))), 'prize'
] = 0 * 90000 + 0 * 200 + 36 * 5

In [98]:
df_matched_numbers.sample(3)

tickets_id            drawing_id  line_id bet_type  \
1819   5eef90ab59fce6002ced4235  polishMiniLotto_3892  9.00000   NORMAL   
4389   5ef7a7abb0deeb0027353710  polishMiniLotto_3892  1.00000   NORMAL   
19243  5ef8d2a3311e0b002cfcc56e  polishMiniLotto_3892  2.00000   NORMAL   

              numbers          numbers_list matched_numbers  \
1819      5,7,9,24,29     [5, 7, 9, 24, 29]              []   
4389   12,19,24,28,37  [12, 19, 24, 28, 37]            [19]   
19243    6,8,18,31,38    [6, 8, 18, 31, 38]              []   

      matched_numbers_count  prize  
1819                      0      0  
4389                      1      0  
19243                     0      0

In [99]:
df_matched_numbers.describe()

line_id       prize
count 22351.00000 22351.00000
mean      4.62158     0.20648
std       3.45530     7.73273
min       1.00000     0.00000
25%       1.00000     0.00000
50%       4.00000     0.00000
75%       7.00000     0.00000
max      12.00000   920.00000

In [100]:
df_matched_numbers.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 22351 entries, 0 to 22350
Data columns (total 9 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   tickets_id             22351 non-null  object 
 1   drawing_id             22351 non-null  object 
 2   line_id                22351 non-null  float64
 3   bet_type               22351 non-null  object 
 4   numbers                22351 non-null  object 
 5   numbers_list           22351 non-null  object 
 6   matched_numbers        22351 non-null  object 
 7   matched_numbers_count  22351 non-null  object 
 8   prize                  22351 non-null  int64  
dtypes: float64(1), int64(1), object(7)
memory usage: 1.5+ MB


In [101]:
df_matched_numbers.to_csv(OUTPUTS + "\\df_matched_numbers.csv")

## df_matched_numbers profiling

In [102]:
df_matched_numbers_profile = ProfileReport(df_matched_numbers, explorative=True)

In [103]:
df_matched_numbers_profile.to_file(output_file=OUTPUTS + "\\df_matched_numbers_profile.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [104]:
df_matched_numbers_profile.to_notebook_iframe()

## Questions:

### 0. 

In [105]:
tickets.head(3)

drawing_id         drawingdate                tickets_id  shares  \
0  polishMiniLotto_3892 2020-06-28 19:50:00  5e3fdd6c6d0034002c62ce11 1.00000   
1  polishMiniLotto_3892 2020-06-28 19:50:00  5924d5c5b9b5ab77047f1238 1.00000   
2  polishMiniLotto_3892 2020-06-28 19:50:00  5ea0e78a0fa635002cfbab70 1.00000   

   total_shares  fraction participation_state  
0       1.00000   1.00000            FINISHED  
1       1.00000   1.00000            FINISHED  
2       1.00000   1.00000            FINISHED

In [106]:
tickets.tail(3)

drawing_id         drawingdate                tickets_id  \
5739  polishMiniLotto_3892 2020-06-28 19:50:00  5ef8a54fc5d9eb002705e1df   
5740  polishMiniLotto_3892 2020-06-28 19:50:00  5ef8a555b0deeb0027356946   
5741  polishMiniLotto_3892 2020-06-28 19:50:00  5ef8a567c5d9eb002705e1f0   

      shares  total_shares  fraction participation_state  
5739 1.00000       1.00000   1.00000            FINISHED  
5740 1.00000       1.00000   1.00000            FINISHED  
5741 1.00000       1.00000   1.00000            FINISHED

In [107]:
df_matched_numbers.sample(3)

tickets_id            drawing_id  line_id bet_type  \
1779   5eef5a8cce3123002cdeeea9  polishMiniLotto_3892 10.00000   NORMAL   
20528  5ef8dc3a89dd2a002c12e0bc  polishMiniLotto_3892  2.00000   NORMAL   
5896   5ef7a7bbc5d9eb002705b315  polishMiniLotto_3892  4.00000   NORMAL   

              numbers          numbers_list matched_numbers  \
1779     1,3,18,28,35    [1, 3, 18, 28, 35]              []   
20528  14,18,28,35,38  [14, 18, 28, 35, 38]              []   
5896   13,17,28,30,37  [13, 17, 28, 30, 37]              []   

      matched_numbers_count  prize  
1779                      0      0  
20528                     0      0  
5896                      0      0

In [108]:
prizes = df_matched_numbers[["tickets_id", "drawing_id", "line_id", "bet_type", "numbers", "matched_numbers_count", "prize"]]

In [109]:
prizes.head(3)

tickets_id            drawing_id  line_id bet_type  \
0  550b11cee4b07489e9e03217  polishMiniLotto_3892  1.00000   NORMAL   
1  553a820ce4b0a8a498faab3a  polishMiniLotto_3892  1.00000   NORMAL   
2  553bcf70e4b0f1fa230477c8  polishMiniLotto_3892  1.00000   NORMAL   

         numbers matched_numbers_count  prize  
0     3,4,6,7,36                     0      0  
1  7,25,29,33,39                     1      0  
2  4,13,24,26,29                     0      0

In [110]:
prizes.tail(3)

tickets_id            drawing_id  line_id bet_type  \
22348  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892 10.00000   NORMAL   
22349  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892 11.00000   NORMAL   
22350  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892 12.00000   NORMAL   

              numbers matched_numbers_count  prize  
22348   8,19,21,28,33                     3      5  
22349   3,10,12,20,39                     0      0  
22350  14,24,25,28,31                     0      0

In [111]:
q0 = """
WITH

    v_tickets AS (
        SELECT
            drawing_id,
            drawingdate,
            tickets_id,
            shares,
            total_shares,
            fraction,
            participation_state

        FROM tickets
        )
   
SELECT
    COUNT(DISTINCT tickets_id) AS tickets_id

FROM v_tickets as vt
"""

In [112]:
ps.sqldf(q0, locals())

tickets_id
0        5742

In [113]:
q1 = """
WITH

    v_prizes AS (
        SELECT
            tickets_id,
            drawing_id,
            line_id,
            bet_type,
            numbers,
            matched_numbers_count as Tier,
            prize

        FROM prizes
        )
   
SELECT
    COUNT(tickets_id) AS tickets_id

FROM v_prizes as vt
"""

In [114]:
ps.sqldf(q1, locals())

tickets_id
0       22351

In [115]:
q3 = """
WITH

    v_prizes AS (
        SELECT
            tickets_id,
            drawing_id,
            line_id,
            bet_type,
            numbers,
            matched_numbers_count as Tier,
            prize

        FROM prizes
        ),

    v_tickets AS (
        SELECT DISTINCT
            tickets_id,
            fraction

        FROM tickets
        )


SELECT
    vp.*,
    vt.*,
    vt.fraction * vp.prize AS prize_x_fraction


FROM v_prizes as vp
LEFT JOIN v_tickets as vt

ON
vp.tickets_id = vt.tickets_id

ORDER BY
prize DESC
"""

In [116]:
sql_3 = ps.sqldf(q3, locals())

In [117]:
sql_3

tickets_id            drawing_id  line_id bet_type  \
0      5ef7b6821aa8bb002cc0cd37  polishMiniLotto_3892  1.00000    S0800   
1      5ee855b9353c30002c7f4b65  polishMiniLotto_3892  1.00000   NORMAL   
2      5ef7a7a7b0deeb00273536bc  polishMiniLotto_3892  5.00000   NORMAL   
3      5ef7bfcffd324f002ca878b1  polishMiniLotto_3892 10.00000   NORMAL   
4      5ef85e80eaf7fe002c77edff  polishMiniLotto_3892  2.00000   NORMAL   
...                         ...                   ...      ...      ...   
22346  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892  7.00000   NORMAL   
22347  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892  8.00000   NORMAL   
22348  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892  9.00000   NORMAL   
22349  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892 11.00000   NORMAL   
22350  5ef8f406b8b7d8002df3b0c3  polishMiniLotto_3892 12.00000   NORMAL   

                     numbers  Tier  prize                tickets_id  fraction  \
0      5,8,11,16,17,19,21,33     4    920  5ef7b6821aa8bb002cc0cd37   0.03333   
1              9,11,19,33,42     4    200  5ee855b9353c30002c7f4b65   1.00000   
2             11,19,21,25,33     4    200  5ef7a7a7b0deeb00273536bc   1.00000   
3              9,11,19,33,42     4    200  5ef7bfcffd324f002ca878b1   1.00000   
4             11,19,21,33,39     4    200  5ef85e80eaf7fe002c77edff   1.00000   
...                      ...   ...    ...                       ...       ...   
22346           1,5,22,34,38     0      0  5ef8f406b8b7d8002df3b0c3   1.00000   
22347         13,16,26,38,40     0      0  5ef8f406b8b7d8002df3b0c3   1.00000   
22348            1,2,7,31,36     0      0  5ef8f406b8b7d8002df3b0c3   1.00000   
22349          3,10,12,20,39     0      0  5ef8f406b8b7d8002df3b0c3   1.00000   
22350         14,24,25,28,31     0      0  5ef8f406b8b7d8002df3b0c3   1.00000   

       prize_x_fraction  
0              30.66360  
1             200.00000  
2             200.00000  
3             200.00000  
4             200.00000  
...                 ...  
22346           0.00000  
22347           0.00000  
22348           0.00000  
22349           0.00000  
22350           0.00000  

[22351 rows x 10 columns]

In [118]:
sql_3.shape

(22351, 10)

In [119]:
sql_3.describe()

line_id        Tier       prize    fraction  prize_x_fraction
count 22351.00000 22351.00000 22351.00000 22351.00000       22351.00000
mean      4.62158     0.62194     0.20648     0.99216           0.15762
std       3.45530     0.71122     7.73273     0.08302           4.49378
min       1.00000     0.00000     0.00000     0.01111           0.00000
25%       1.00000     0.00000     0.00000     1.00000           0.00000
50%       4.00000     0.00000     0.00000     1.00000           0.00000
75%       7.00000     1.00000     0.00000     1.00000           0.00000
max      12.00000     4.00000   920.00000     1.00000         200.00000

In [120]:
sql_3["prize"].describe()

count   22351.00000
mean        0.20648
std         7.73273
min         0.00000
25%         0.00000
50%         0.00000
75%         0.00000
max       920.00000
Name: prize, dtype: float64

In [121]:
sql_3["prize_x_fraction"].describe()

count   22351.00000
mean        0.15762
std         4.49378
min         0.00000
25%         0.00000
50%         0.00000
75%         0.00000
max       200.00000
Name: prize_x_fraction, dtype: float64

In [122]:
python_solution = sql_3

In [123]:
python_solution.to_csv(OUTPUTS + "\\python_solution.csv")